In [30]:
#modulos
import json
from prettyprinter import pprint
import os
import re
from pymongo import MongoClient, InsertOne, GEO2D
from bson.son import SON
import pymongo
import pandas as pd
import csv
from pyproj import Proj
import utm
import re
from datetime import datetime
import numpy as np



In [2]:
#credenciales de MOngodb
client=pymongo.MongoClient("localhost", 27017) #'mongodb://localhost:27017/'
db = client.proyecto_BG3
collection_trafico=db.trafico_BG3
#activar la siguiente linea si se incluirán todas las estaciones en una sola coleccion
#collection_estaciones=db.estaciones_BG3

In [36]:
#URI de todos los directorios de trafico
path_trafico='/home/santiago/Desktop/shared_bigdata_def/mayo'
#path_meteoro='/home/vagrant/Escritorio/scripts_bigdata/datos_meteoro'
path_estaciones='/home/santiago/Desktop/shared_bigdata_def/estaciones'
#definicion de proyeccion
#myProj=Proj('+proj=utm +zone=30 +ellps=GRS80 +towgs84=0,0,0,0,0,0,0 +units=m +no_defs +type=crs')


In [13]:
#funciones para caga de estaciones metereologicas en diferentes colecciones

def import_csv_mongodb(path_csv):
    path_files=[]
    for file in os.listdir(path_csv):
        
        path_files.append(os.path.join(path_estaciones, file))
        #print(path_files)
        #evalua si el nombre del fichero coincide con alguna de las estaciones del
        #siguiente diccionario longitud, latitud en formato array que espera mongodb
        estaciones={'pista_silla':[-0.376653,39.458060],'vivers':[-0.369550,39.479488],
                    'politecnic':[-0.337407,39.479621],'av_francia':[-0.342689,39.457504],
                    'moli_sol':[-0.408558,39.481138],'bulevard_sud':[-0.396313,39.450378],
                    'centre':[-0.376384,39.470718],'nazaret': [-0.333289,39.448554],
                    'conselleria_meteo': [-0.404878,39.472034],'port_llit':[-0.328945,39.450518],
                    'olivereta':[-0.406037,39.469238], 'port_moll':[-0.323217,39.459264]
                    }
    contador=0 #un contador para saber cuantas estaciones carga 

    for file in path_files:
        #nombre de la estacion en el path
        file_name=os.path.splitext(os.path.basename(file))[0]
        #se almacenará en una coleccion distinta por cada fichero de estacion meteorologica
        collection_estacion=db[file_name]
        
        if file.endswith(('txt','csv')):
            
            df=pd.read_csv(file, header=0, sep='\t', encoding='latin1',skiprows=3)  
            df=df.iloc[1:]
            #crear un campo nuevo para fecha y hora
            df['HORA']=df['HORA'].astype(int)
            df['HORA']=df['HORA'].astype(str)
            df['FECHA_COMPLETA'] = df.FECHA + 'H' + df.HORA
            df.drop(['FECHA','HORA'],axis=1, inplace=True)
            df['FECHA_COMPLETA']=pd.to_datetime(df['FECHA_COMPLETA'],errors='coerce', format='%d/%m/%YH%H')

            #filtrar solo los datos del mes de mayo
            df= df[(df['FECHA_COMPLETA']>="2023-05-01")&(df['FECHA_COMPLETA']<"2023-06-01")]

            contador +=1
        #crea el diccionario para guardar solo un par de coordenadas y todas las lecturas
        estaciones_dict={}
        for estacion, coords in estaciones.items():
                if estacion == file_name:
                    print(estacion)
                    estaciones_dict['nombre']=estacion
                    estaciones_dict['coordinates']=coords
                    print(estaciones_dict)
                    

        #print(df.head())
        #print(df.shape)
        print(file_name, " " , "# estacion: ", contador)
        js=df.to_json(orient='records',date_format='iso')
        #print(js)
        parsed=json.loads(js)
        #print(parsed)
        estaciones_dict['lecturas']=parsed
        
        print(json.dumps(estaciones_dict, indent=4)[:])

        #almacenar en cada coleccion
        collection_estacion.insert_one(estaciones_dict)
                    
           
import_csv_mongodb(path_estaciones)                           




av_francia
{'nombre': 'av_francia', 'coordinates': [-0.342689, 39.457504]}
av_francia   # estacion:  1
{
    "nombre": "av_francia",
    "coordinates": [
        -0.342689,
        39.457504
    ],
    "lecturas": [
        {
            "Veloc.": "0,7",
            "Direc.": "51",
            "PM2.5": "6",
            "SO2": "3",
            "CO": "0,1",
            "NO": "2",
            "NO2": "1",
            "PM10": "7",
            "NOx": "4",
            "O3": "87",
            "FECHA_COMPLETA": "2023-05-01T00:00:00.000"
        },
        {
            "Veloc.": "1,4",
            "Direc.": "48",
            "PM2.5": "5",
            "SO2": "4",
            "CO": "0,1",
            "NO": "2",
            "NO2": "1",
            "PM10": "6",
            "NOx": "4",
            "O3": "88",
            "FECHA_COMPLETA": "2023-05-01T01:00:00.000"
        },
        {
            "Veloc.": "1,6",
            "Direc.": "63",
            "PM2.5": "6",
            "SO2": "4",
         

In [37]:
#funciones para carga de datos de trafico

#funcion para transformar desde UTM a latlon wgs84
def converter(i):
    try:
        tpl = utm.to_latlon(i['xcoord'],i['ycoord'],30,'N')
        return tpl #lat y lon
    except Exception as e:
        return None
    
#carga datos de trafico
def import_csv_mongodb_trafico(path_csv):
    path_files=[]
    for file in os.listdir(path_csv):
        
        path_files.append(os.path.join(path_trafico, file))
    
        
    contador=0 #un contador para saber cuantas estaciones carga 

    df=pd.DataFrame()
    sensor_coords = dict()
    for file in path_files:
        
        
        
        if file.endswith(('txt','csv')):
            try:
                #nombre del fichero que funge como hora segun requerimientos del proyecto
                match = re.search(r'/([^/]+)\.[^.]+$', file)
                if match:
                    file_name = match.group(1)
                    print(file_name)
                
                df1=pd.read_csv(file, header=0, sep=';', encoding='latin1')  
                contador +=1
                print('contador ficheros: ',contador)

                #usar como hora el nombre del fichero para el formato "2023-5-1T0H0m"
                df1['HORA_file']=file_name 
                df1['HORA']=pd.to_datetime(df1['HORA_file'],errors='coerce', format='%Y-%m-%dT%HH%Mm')

                #transformacion de la hora por el campo con la hora presente dentro fichero
                #df1['HORA']=df1['modified'].str.split('+').str[0]
                #df1['HORA']=pd.to_datetime(df1['HORA_file'],errors='coerce', format='%Y-%m-%dT%H:%M:%S')
            
                #transformacion de coordenadas de UTM a WGS84
                #utm.to_latlon(easting(x),northing(y),zonenumber,zoneletter)   
                df1['ycoord']=df1['ycoord'].astype(int)
                df1['xcoord']=df1['xcoord'].astype(int)
              
                df1['coords'] = df1.apply(converter, axis=1)

                #convierte a series y ya es más facil extraer los valores de la tupla
                #(lat, lon) que devuelve utm. Es la forma de manipular una tupla en Pandas
                df1[['lat','lon']] = df1['coords'].apply(lambda x: pd.Series(x))

                
                #recomponer una string con lon y lat en formato array que espera mongodb
                df1['coords'] = df1.apply(lambda row: [row['lon'], row['lat']], axis=1)

                #a los valores con cooredenadas nulas hacer el respectivo llenado
                
                #añadir al diccionario las coordenadas del sensor
                #evalua si ya esta presente y si es distinta o no a 0 en ambos componentes
                #latitud y longitud
                for index, row in df1.iterrows():
                    sensor = row['sensor']
                    coords = row['coords']
                     
                    if sensor not in sensor_coords:
                        if not np.isnan(coords[0]) and coords[0] != 0:
                            sensor_coords[sensor] = coords
                        else:
                            sensor_coords[sensor] = [0, 0]
                    
                
                #mapeo del diccionario en donde hay coordenadas nulas
                
                df1['coords'] = df1['sensor'].map(sensor_coords).fillna(df1['coords'])
            
                #limpiar las columnas innecesarias
                df1.drop(['modified','HORA_file','uri','ycoord','xcoord','angulo','lat','lon','xcoord','ycoord'], axis=1,inplace=True)
                # print(df1.head())
                # print(df1.tail())            
                #concatenar el dataframe de cada fichero a uno solo dataframe total
                df = pd.concat([df,df1], ignore_index=True)
            except Exception as e:
                print(file, 'error:', str(e))
                continue

     #debugging si hay errores en el mapeo de las coordenadas 
    #pprint(sensor_coords[2028])  #sensor con coordenadas en algunos ficheros
    #pprint(sensor_coords[2014])  #sensor sin ninguna coordenada en ningun fichero
    #pprint(sensor_coords[113])   #sensor con coordenadas siempre
    #verificar el sensor que no tiene coordenadas en ningun fichero
    #print(df[df['sensor']==2014])
    #print(df[df['sensor']==2018])
    #print(df[df['sensor']==113])
    #print(sensor_coords.keys())
    #debugging si hay intensidad con errores de lectura en la fuenta
    df.loc[(df["intensidad"]==-1) | (df["intensidad"]==5000), "intensidad"] = None
    #comprobación intensidad
    #print(df.loc[(df["intensidad"]==-1) | (df["intensidad"]== 5000)] )

    #revisar el df de salida
    #print(df.head())
    #print(df.dtypes)
    #print(df.shape)
    
    #conversion del df a formato json    
    js=df.to_json(orient='records',date_format='iso')
    parsed=json.loads(js)
    #print(json.dumps(parsed, indent=4)[:])
                
    collection_trafico.insert_many(parsed) 
                    
          
import_csv_mongodb_trafico(path_trafico)    



2023-5-10T0H0m
contador ficheros:  1
2023-5-10T0H15m
contador ficheros:  2
2023-5-10T0H30m
contador ficheros:  3
2023-5-10T0H45m
contador ficheros:  4
2023-5-10T10H0m
contador ficheros:  5
2023-5-10T10H15m
contador ficheros:  6
2023-5-10T10H30m
contador ficheros:  7
2023-5-10T10H45m
contador ficheros:  8
2023-5-10T11H0m
contador ficheros:  9
2023-5-10T11H15m
contador ficheros:  10
2023-5-10T11H30m
contador ficheros:  11
2023-5-10T11H45m
contador ficheros:  12
2023-5-10T12H0m
contador ficheros:  13
2023-5-10T12H15m
contador ficheros:  14
2023-5-10T12H30m
contador ficheros:  15
2023-5-10T12H45m
contador ficheros:  16
2023-5-10T13H0m
contador ficheros:  17
2023-5-10T13H15m
contador ficheros:  18
2023-5-10T13H30m
contador ficheros:  19
2023-5-10T13H45m
contador ficheros:  20
2023-5-10T14H0m
contador ficheros:  21
2023-5-10T14H15m
contador ficheros:  22
2023-5-10T14H30m
contador ficheros:  23
2023-5-10T14H45m
contador ficheros:  24
2023-5-10T15H0m
contador ficheros:  25
2023-5-10T15H15m
con

In [29]:
#debug funcion datos de trafico
import re
#funcion para transformar desde UTM a latlon wgs84
def converter(i):
    try:
        tpl = utm.to_latlon(i['xcoord'],i['ycoord'],30,'N')
        return tpl #lat y lon
    except Exception as e:
        return None
    
#carga datos de trafico
def import_csv_mongodb_trafico(path_csv):
    path_files=[]
    for file in os.listdir(path_csv):
        
        path_files.append(os.path.join(path_trafico, file))

    df=pd.DataFrame()
    sensor_coords = dict()
    for file in path_files:
        
        
        if file.endswith(('txt','csv')):
            try:
                   
                #capturar el nombre del fichero con una regex
                #busca un "/" luego captura 1 o más caracteres que no sean "/"" ([^/]+) que precedan
                #un punto "\." luego encuentra 1 o más caracteres que no sean punto [^.]+ 
                # hasta el final de la cadena "$"

                match = re.search(r'/([^/]+)\.[^.]+$', file)
                if match:
                    file_name = match.group(1)
                    print(file_name)
                            
                df1=pd.read_csv(file, header=0, sep=';', encoding='latin1')  
                
            
                
                #usar como hora el nombre del fichero
                #hora=file
                #transformacion de la hora
                #df1['HORA']=df1['modified'].str.split('+').str[0]
                #df1['HORA']=pd.to_datetime(df1['HORA'],errors='coerce', format='%Y-%m-%dT%H:%M:%S')
            except Exception as e:
                print(file, 'error:', str(e))
                continue

import_csv_mongodb_trafico(path_trafico)    

2023-5-1T0H0m
2023-5-1T0H15m
2023-5-1T0H30m
2023-5-1T0H45m
2023-5-1T1H0m
2023-5-1T1H15m
2023-5-1T1H30m
2023-5-1T1H45m
2023-5-1T2H0m
2023-5-1T2H15m
2023-5-1T2H30m
2023-5-1T2H45m
2023-5-1T3H0m
2023-5-1T3H15m
2023-5-1T3H30m
2023-5-1T3H45m
2023-5-1T4H0m
2023-5-1T4H15m
2023-5-1T4H30m
2023-5-1T4H45m
2023-5-1T5H0m
2023-5-1T5H15m
2023-5-1T5H30m
2023-5-1T5H45m
2023-5-1T6H0m
2023-5-1T6H15m
2023-5-1T6H30m
2023-5-1T6H45m
